# Prerequisites

Pull down them dependencies!

In [ ]:
from google.colab import drive
drive.mount('/content/drive')

Mounted at /content/drive


In [ ]:
!git clone https://github.com/facebookresearch/audiocraft.git
%cd audiocraft
!pip install -e .
!pip install dora-search
!pip install numba
!pip install markovify

Cloning into 'audiocraft'...
remote: Enumerating objects: 1426, done.
remote: Total 1426 (delta 0), reused 0 (delta 0), pack-reused 1426
Receiving objects: 100% (1426/1426), 1.95 MiB | 9.99 MiB/s, done.
Resolving deltas: 100% (781/781), done.
/content/audiocraft
Obtaining file:///content/audiocraft
  Preparing metadata (setup.py) ... done
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 32.9/32.9 MB 30.4 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 44.6/44.6 kB 5.2 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 72.4/72.4 kB 8.7 MB/s eta 0:00:00
  Installing build dependencies ... done
  Getting requirements to build wheel ... done
  Preparing metadata (pyproject.toml) ... done
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 154.5/154.5 kB 18.7 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 59.6/59.6 kB 8.3 MB/s eta 0:00:00
  Preparing metadata (setup.py) ... done
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 143.3/143.3 kB 16.7 MB/s eta 0:00

  Preparing metadata (setup.py) ... done
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 235.5/235.5 kB 3.0 MB/s eta 0:00:00
  Created wheel for markovify: filename=markovify-0.9.4-py3-none-any.whl size=18606 sha256=98772f9323bd9fe5b8b04985076cba77a4d431a7c7f62f7d75d896425c8fa573
  Stored in directory: /root/.cache/pip/wheels/ca/8c/c5/41413e24c484f883a100c63ca7b3b0362b7c6f6eb6d7c9cc7f
Successfully built markovify


In [ ]:
!cp /content/drive/MyDrive/ibos-gpt-mm.json /content/
!cp -r /content/drive/MyDrive/gregorian-checkpoint /content/

In [ ]:
%cd /content

/content


In [ ]:
# import markovify
from audiocraft.data.audio import audio_write
import IPython.display as ipd
from audiocraft.models import MusicGen
import numpy as np
# from transformers import T5Tokenizer

# Generate

First, to make prompts:

In [ ]:
markov_model = None
with open("/content/ibos-gpt-mm.json", "r") as f:
  json = f.read()
  markov_model = markovify.Text.from_json(json)

In [ ]:
prompt = "God" # @param {type:"string"}

markov_model.make_sentence_with_start(prompt, strict=False)

'God is negative in the sense that in academic circles #chatGPT is the first such ban at a college in the country. LItalia ferma ChatGpt. OpenAI sospende il servizio nel paese.'

Then we can prompt MusicGen:

In [ ]:
!mv /content/gregorian-checkpoint /content/finetune
!mkdir /content/checkpoints
!mv /content/finetune /content/checkpoints/finetune

In [ ]:
!pip install transformers

In [ ]:
musicgen = MusicGen.get_pretrained('/content/checkpoints/finetune')
musicgen.set_generation_params(duration=12)

spiece.model:   0%|          | 0.00/792k [00:00<?, ?B/s]

tokenizer.json:   0%|          | 0.00/1.39M [00:00<?, ?B/s]

config.json:   0%|          | 0.00/1.21k [00:00<?, ?B/s]

model.safetensors:   0%|          | 0.00/892M [00:00<?, ?B/s]

config.json:   0%|          | 0.00/758 [00:00<?, ?B/s]

model.safetensors:   0%|          | 0.00/236M [00:00<?, ?B/s]

/usr/local/lib/python3.10/dist-packages/torch/nn/utils/weight_norm.py:30: UserWarning: torch.nn.utils.weight_norm is deprecated in favor of torch.nn.utils.parametrizations.weight_norm.
  warnings.warn("torch.nn.utils.weight_norm is deprecated in favor of torch.nn.utils.parametrizations.weight_norm.")


In [ ]:
%cd /content/audiocraft
%env USER=kowalk

/content/audiocraft
env: USER=kowalk


In [ ]:
from audiocraft.data.audio import audio_write
import IPython.display as ipd
from audiocraft.models import MusicGen
import numpy as np

# load your finetune
musicgen = MusicGen.get_pretrained('/content/checkpoints/finetune')
musicgen.set_generation_params(duration=16)

OSError: Can't load tokenizer for 't5-base'. If you were trying to load it from 'https://huggingface.co/models', make sure you don't have a local directory with the same name. Otherwise, make sure 't5-base' is the correct path to a directory containing all relevant files for a T5Tokenizer tokenizer.

In [ ]:
prompt_m = "Sacred Oath of the Weasel tradition." # @param {type:"string"}

wavs = musicgen.generate([prompt_m] * 4)

# save and display generated audio
for idx, one_wav in enumerate(wavs):
    audio_write(f'{idx}', one_wav.cpu(), musicgen.sample_rate, strategy="loudness", loudness_compressor=True)
    ipd.display(ipd.Audio(one_wav.cpu(), rate=32000))